# Embedding Text with Azure OpenAI and GPU based KNN

The Azure OpenAI service can be used to solve a large number of natural language tasks through prompting the completion API. To make it easier to scale your prompting workflows from a few examples to large datasets of examples we have integrated the Azure OpenAI service with the distributed machine learning library [Spark Rapids ML](https://github.com/NVIDIA/spark-rapids-ml/). This integration makes it easy to use the [Apache Spark](https://spark.apache.org/) distributed computing framework to process millions of prompts with the OpenAI service. This tutorial shows how to apply large language models to generate embeddings for large datasets of text. This demo is based on "Quickstart - OpenAI Embedding" notebook with NVIDIA GPU accelerated KNN.

**Note**: Running the notebook with the demo dataset (Step 4) will generate the same results as CPU based “Quickstart - OpenAI Embedding” notebook. To see  GPU acceleration you need to run query against bigger embeddings. 
For example, running 100K rows dataset will give 6x acceleration and consume less than 10x memory on 2 nodes NVIDIA T4 cluster compare to AMD Epic (Rome) 2 nodes CPU cluster.

## Step 1: Prerequisites

The key prerequisites for this quickstart include a working Azure OpenAI resource, and an Apache Spark cluster with SynapseML installed. We suggest creating a Synapse workspace, but an Azure Databricks, HDInsight, or Spark on Kubernetes, or even a python environment with the `pyspark` package will work. 

1. An Azure OpenAI resource – request access [here](https://customervoice.microsoft.com/Pages/ResponsePage.aspx?id=v4j5cvGGr0GRqy180BHbR7en2Ais5pxKtso_Pz4b1_xUOFA5Qk1UWDRBMjg0WFhPMkIzTzhKQ1dWNyQlQCN0PWcu) before [creating a resource](https://docs.microsoft.com/en-us/azure/cognitive-services/openai/how-to/create-resource?pivots=web-portal#create-a-resource)
1. [Create a Synapse workspace](https://docs.microsoft.com/en-us/azure/synapse-analytics/get-started-create-workspace)
1. [Create a serverless Apache Spark pool](https://docs.microsoft.com/en-us/azure/synapse-analytics/get-started-analyze-spark#create-a-serverless-apache-spark-pool)


## Step 2: Import this guide as a notebook

The next step is to add this code into your Spark cluster. You can either create a notebook in your Spark platform and copy the code into this notebook to run the demo. Or download the notebook and import it into Synapse Analytics

1.	[Download this demo as a notebook](https://github.com/microsoft/SynapseML/blob/master/notebooks/features/cognitive_services/CognitiveServices%20-%20OpenAI%20Embedding.ipynb) (click Raw, then save the file)
1.	Import the notebook [into the Synapse Workspace](https://docs.microsoft.com/en-us/azure/synapse-analytics/spark/apache-spark-development-using-notebooks#create-a-notebook) or if using Databricks [into the Databricks Workspace](https://docs.microsoft.com/en-us/azure/databricks/notebooks/notebooks-manage#create-a-notebook)
1. Install SynapseML on your cluster. Please see the installation instructions for Synapse at the bottom of [the SynapseML website](https://microsoft.github.io/SynapseML/). Note that this requires pasting an additional cell at the top of the notebook you just imported
3. To run the notebook on Databricks add the following Init Script:
            
            #!/bin/bash
            # set portion of path below after /dbfs/ to dbfs zip file location
            SPARK_RAPIDS_ML_ZIP=/dbfs/path/to/zip/file
            # IMPORTANT: specify RAPIDS_VERSION fully 23.10.0 and not 23.10
            # also in general, RAPIDS_VERSION (python) fields should omit any leading 0 in month/minor field (i.e. 23.8.0 and not 23.08.0)
            # while SPARK_RAPIDS_VERSION (jar) should have leading 0 in month/minor (e.g. 23.08.2 and not 23.8.2)
            RAPIDS_VERSION=23.10.0
            SPARK_RAPIDS_VERSION=23.10.0

            curl -L https://repo1.maven.org/maven2/com/nvidia/rapids-4-spark_2.12/${SPARK_RAPIDS_VERSION}/rapids-4-spark_2.12-${SPARK_RAPIDS_VERSION}-cuda11.jar -o /databricks/jars/rapids-4-spark_2.12-${SPARK_RAPIDS_VERSION}.jar

            # install cudatoolkit 11.8 via runfile approach
            wget https://developer.download.nvidia.com/compute/cuda/11.8.0/local_installers/cuda_11.8.0_520.61.05_linux.run
            sh cuda_11.8.0_520.61.05_linux.run --silent --toolkit

            # reset symlink and update library loading paths
            rm /usr/local/cuda
            ln -s /usr/local/cuda-11.8 /usr/local/cuda

            # upgrade pip
            /databricks/python/bin/pip install --upgrade pip

            # install cudf, cuml and their rapids dependencies
            # using ~= pulls in latest micro version patches
            /databricks/python/bin/pip install cudf-cu11~=${RAPIDS_VERSION} \
                cuml-cu11~=${RAPIDS_VERSION} \
                pylibraft-cu11~=${RAPIDS_VERSION} \
                rmm-cu11~=${RAPIDS_VERSION} \
                --extra-index-url=https://pypi.nvidia.com

            # install spark-rapids-ml
            /databricks/python/bin/pip install spark-rapids-ml

4.	Connect your notebook to a cluster and follow along, editing and rnnung the cells below.

## Step 3: Fill in your service information

Next, please edit the cell in the notebook to point to your service. In particular set the `service_name`, `deployment_name`, `location`, and `key` variables to match those for your OpenAI service:

In [ ]:
from synapse.ml.core.platform import find_secret

# Fill in the following lines with your service information
# Learn more about selecting which embedding model to choose: https://openai.com/blog/new-and-improved-embedding-model
service_name = "synapseml-openai"
deployment_name_embeddings = "text-embedding-ada-002"

key = find_secret(
    secret_name="openai-api-key", keyvault="mmlspark-build-keys"
)  # please replace this with your key as a string

assert key is not None and service_name is not None

## Step 4: Load Data

In this demo we will explore a dataset of fine food reviews

In [ ]:
import pyspark.sql.functions as F

df = (
    spark.read.options(inferSchema="True", delimiter=",", header=True)
    .csv("wasbs://publicwasb@mmlspark.blob.core.windows.net/fine_food_reviews_1k.csv")
    .repartition(5)
)

df = df.withColumn(
    "combined",
    F.format_string("Title: %s; Content: %s", F.trim(df.Summary), F.trim(df.Text)),
)

display(df)

id Time ProductId UserId Score Summary Text combined 529 1351209600 B0007A0AQW A1HHNY1GVD3UIS 5 my dogs love the peanut butter! First off, read the ingredients, no crazy words I can't pronounce, which means it's all natural! I got the peanut butter treats for my two children: husky/shepherd and a lab/shepherd mix, and they can't get enough of them. Plus, on Amazon, this is such a great value for 16oz. Beats petsmart for sure! I'll be looking for more Zuke's products now that I've discovered them. Thanks Zuke's! Title: my dogs love the peanut butter!; Content: First off, read the ingredients, no crazy words I can't pronounce, which means it's all natural! I got the peanut butter treats for my two children: husky/shepherd and a lab/shepherd mix, and they can't get enough of them. Plus, on Amazon, this is such a great value for 16oz. Beats petsmart for sure! I'll be looking for more Zuke's products now that I've discovered them. Thanks Zuke's! 132 1351123200 B0012KB3ZI AIFGUCOUOOFJ3 5 Great for my older cat My older cat just stopped eating the dry kibble food a few months ago. She used to get Fancy Feast as a treat only, but now it is all she will eat. A lot of canned cat food smells repulsive! Fancy Feast actually looks & smells decent. The cat knows which cabinet I keep her food in & she sprints to the kitchen when she hears it open. Title: Great for my older cat; Content: My older cat just stopped eating the dry kibble food a few months ago. She used to get Fancy Feast as a treat only, but now it is all she will eat. A lot of canned cat food smells repulsive! Fancy Feast actually looks & smells decent. The cat knows which cabinet I keep her food in & she sprints to the kitchen when she hears it open. 764 1351209600 B001HTIUDC A27RDA09KDYVGY 5 Delicious This product is a great alternative to peanut butter, or any butter. I like it just as much as I ever liked peanut butter. It has a similar nutty flavor, with a great contrast of salty and sweet. The shipping was fast, and its a delicious and healthy snack you can eat with just about anything! Title: Delicious; Content: This product is a great alternative to peanut butter, or any butter. I like it just as much as I ever liked peanut butter. It has a similar nutty flavor, with a great contrast of salty and sweet. The shipping was fast, and its a delicious and healthy snack you can eat with just about anything! 833 1351209600 B0054ES1NK A25QCYSED869Q3 5 If you like mint candy...... This is the best hard mint candy in the world. Expensive, though. I can't find it in stores. Anyone know where I can get it off-line? Title: If you like mint candy......; Content: This is the best hard mint candy in the world. Expensive, though. I can't find it in stores. Anyone know where I can get it off-line? 495 1351209600 B0012VSXIM A2TOUMUWSN7FJY 5 Good & Plenty Licorice Candy If you like licorice you will love this candy. I can remember eating this candy from a box at the local movie theatre when I was a kid and it is still just as good. Title: Good & Plenty Licorice Candy; Content: If you like licorice you will love this candy. I can remember eating this candy from a box at the local movie theatre when I was a kid and it is still just as good. 59 1351123200 B0041CH4I4 A4BFKBO2SU9AX 4 Yummy & Great Small Gift If someone who will remain nameless would stop eating all mine, then I wouldn't have had to get the box of 20 Chimes ginger candy tins. But I'm glad I did. The packaging is cute, and makes a great small gift to hand out to a co-worker having a rough day, a client when you visit, or a friend when you stop by to watch the game. The tins are recyclable in most locations. The individually wrapped candies are made with cane sugar and real ginger, no high fructose corn syrup so they are in a way better for you than other candy options. Ginger has anti-inflammatory properties and can settle a stomach and ease hearburn. When's the last time your chocolate bar did that? Title: Yummy & Great Small Gif

## Step 5: Generate Embeddings

We will first generate embeddings for the reviews using the SynapseML OpenAIEmbedding client.

In [ ]:
from synapse.ml.services.openai import OpenAIEmbedding

embedding = (
    OpenAIEmbedding()
    .setSubscriptionKey(key)
    .setDeploymentName(deployment_name_embeddings)
    .setCustomServiceName(service_name)
    .setTextCol("combined")
    .setErrorCol("error")
    .setOutputCol("embeddings")
)

completed_df = embedding.transform(df).cache()
display(completed_df)

id Time ProductId UserId Score Summary Text combined error embeddings 529 1351209600 B0007A0AQW A1HHNY1GVD3UIS 5 my dogs love the peanut butter! First off, read the ingredients, no crazy words I can't pronounce, which means it's all natural! I got the peanut butter treats for my two children: husky/shepherd and a lab/shepherd mix, and they can't get enough of them. Plus, on Amazon, this is such a great value for 16oz. Beats petsmart for sure! I'll be looking for more Zuke's products now that I've discovered them. Thanks Zuke's! Title: my dogs love the peanut butter!; Content: First off, read the ingredients, no crazy words I can't pronounce, which means it's all natural! I got the peanut butter treats for my two children: husky/shepherd and a lab/shepherd mix, and they can't get enough of them. Plus, on Amazon, this is such a great value for 16oz. Beats petsmart for sure! I'll be looking for more Zuke's products now that I've discovered them. Thanks Zuke's! null Map(vectorType -> dense, length -> 1536, values -> List(-0.021949474, -0.010235235, -0.015221966, -0.008828217, -0.009711693, 0.02869007, 0.028087998, -0.03842794, -0.009004912, -0.026399575, 2.636113E-4, 0.027145622, -0.04672607, -0.02636031, -0.012722056, 0.017852763, 0.03853265, 0.017852763, -0.007630616, -0.008402839, -0.0271718, -7.362301E-4, 0.019122351, -0.034187254, -1.3783864E-4, 0.0068911137, 0.018559543, -0.0010814402, -0.017316133, -5.6444306E-4, 0.023101265, 0.003278678, -0.040626813, -0.013153978, -0.002197238, 0.016216695, 0.008010183, -0.0046824235, 0.024986014, -0.031203069, -0.0063675726, 0.021124896, 0.0027338678, -0.007643705, -0.025221609, 0.00547428, -0.016530821, -0.03243339, 0.0027060546, -0.00719215, 0.03403019, 0.020575177, -0.028140351, 0.012794044, -0.007597895, -0.012833309, 6.7160546E-4, 0.0016107078, 0.011210331, -0.03368989, 0.018847492, 0.020509735, -0.02806182, 0.009633162, -0.010896206, -0.024527915, 0.0033359404, 0.019541183, -0.012807132, 0.021308135, 0.0021956018, -0.0040999837, 0.0062988577, 0.008644978, 0.018729694, 0.021582995, -0.020444293, -0.0014282864, 0.01304927, 0.008514092, 0.03206691, -0.015941836, -0.014619894, 0.024030551, 0.012656614, -0.01041193, 0.011308495, 0.0050259978, -0.013965467, -0.020509735, 0.0075717177, 0.0061647003, -0.0019861853, -0.0029841862, -0.022760963, 0.009456467, -8.192605E-4, 0.01148519, -0.004836214, -0.039082367, -0.008324308, -0.0033392126, 0.01274169, -0.0062988577, -0.019318677, 0.0027027826, -0.009783681, -0.0022152346, 0.0051372503, 9.906385E-4, 0.0070089106, 0.017224513, -0.0026242514, -0.022276687, -0.004135977, 0.018481012, -6.7078747E-4, 0.0025277233, 7.963556E-4, 0.010418475, 0.02378187, 0.016151253, 0.052956216, -0.0018602081, 0.015784774, 0.016033456, 7.399113E-4, -0.013455015, 0.020169433, 0.0022528642, 0.03727615, 0.014894754, 0.015797863, -0.015941836, -0.03868971, 0.028978018, 0.0014708241, -0.02556191, 0.011164521, -0.016910387, 0.02395202, 0.03557464, 0.007650249, -0.013396116, 3.9715524E-4, 0.050024383, -0.0032623175, 0.04442249, 0.007224872, -0.001122342, -0.0011231599, -0.005261591, 0.018088356, 0.017590992, -0.0071136192, 6.7283254E-4, 0.01005854, 0.007597895, -0.024986014, 0.02494675, -0.0064428314, -0.0117600495, -0.0078073116, -0.0066587925, 0.008566447, 0.027826227, 0.02565353, -0.0028549368, -0.014174884, 0.002789494, -0.006475553, 0.021975651, -0.023755692, 0.023546275, -0.008867483, 0.0056542475, 0.009096532, -6.2323925E-5, -0.030705703, 0.0071267076, 0.027119445, -0.009024546, 0.019200882, 0.041595366, 0.0054055653, -0.018821314, 0.023284504, -0.012368666, 0.031203069, -0.0024328316, 0.019554272, 0.0064231986, -0.021439021, -0.029789507, -0.63495106, -0.0070285434, 0.02976333, -0.008527181, 0.031229246, 0.0404174, -0.0042145085, -0.0056411587, -0.0098622115, 0.02654355, -0.0015575357, 0.008998368, -0.010817675, 0.0057589556, 0.0054382863, -0.015182701, 0.015627712, -0.05345358, 0.014790045, 1.6984419E-4, -0.022237422, 0.022368306, 0.0039200163, -0.01393929, 0.0187

## Step 6: Reduce Embedding dimensionality for Visualization
We reduce the dimensionality to 2 dimensions using t-SNE decomposition.

In [ ]:
import pandas as pd
from sklearn.manifold import TSNE
import numpy as np

collected = list(completed_df.collect())
matrix = np.array([[r["embeddings"]] for r in collected])[:, 0, :].astype(np.float64)
scores = np.array([[r["Score"]] for r in collected]).reshape(-1)

tsne = TSNE(n_components=2, perplexity=15, random_state=42, init="pca")
vis_dims = tsne.fit_transform(matrix)
vis_dims.shape

## Step 7: Plot the embeddings

We now use t-SNE to reduce the dimensionality of the embeddings from 1536 to 2. Once the embeddings are reduced to two dimensions, we can plot them in a 2D scatter plot. We colour each review by its star rating, ranging from red for negative reviews, to green for positive reviews. We can observe a decent data separation even in the reduced 2 dimensions.

In [ ]:
import matplotlib.pyplot as plt
import matplotlib
import numpy as np

colors = ["red", "darkorange", "gold", "turquoise", "darkgreen"]
x = [x for x, y in vis_dims]
y = [y for x, y in vis_dims]
color_indices = scores - 1

colormap = matplotlib.colors.ListedColormap(colors)
plt.scatter(x, y, c=color_indices, cmap=colormap, alpha=0.3)
for score in [0, 1, 2, 3, 4]:
    avg_x = np.array(x)[scores - 1 == score].mean()
    avg_y = np.array(y)[scores - 1 == score].mean()
    color = colors[score]
    plt.scatter(avg_x, avg_y, marker="x", color=color, s=100)

plt.title("Amazon ratings visualized in language using t-SNE")

## Step 8: Build the query against embeddings

Note: The data types of the ID columns in the document and query dataframes should be the same. For some OpenAI models, users should use separate models for embedding documents and queries. These models are denoted by the "-doc" and "-query" suffixes respectively.

In [ ]:
from pyspark.ml import PipelineModel

embedding_query = (
    OpenAIEmbedding()
    .setSubscriptionKey(key)
    .setDeploymentName(deployment_name_embeddings)
    .setCustomServiceName(service_name)
    .setTextCol("query")
    .setErrorCol("error")
    .setOutputCol("embeddings")
)

query_df = (
    spark.createDataFrame(
        [
            (
                0,
                "desserts",
            ),
            (
                1,
                "disgusting",
            ),
        ]
    )
    .toDF("id", "query")
    .withColumn("id", F.col("id").cast("int"))
)

embedding_query_df = embedding_query.transform(query_df).select("id", "embeddings").cache()

## Step 9: Fit KNN model 
Build KNN model using fit method

In [ ]:
from spark_rapids_ml.knn import NearestNeighbors

rapids_knn = NearestNeighbors(k=10)
rapids_knn.setInputCol("embeddings").setIdCol("id")

rapids_knn_model = rapids_knn.fit(completed_df.select("id", "embeddings"))

## Step 10: Retrieve query results
Find k nearest neighbors

In [ ]:
(_, _, knn_df) = rapids_knn_model.kneighbors(embedding_query_df)

display(knn_df)

query_id indices distances 0 List(47, 747, 182, 726, 591, 214, 29, 983, 255, 428) List(0.60844487, 0.6164042, 0.61805433, 0.62357146, 0.62726676, 0.6278338, 0.63259506, 0.6382284, 0.63868636, 0.6396766) 1 List(937, 479, 887, 197, 277, 60, 617, 188, 940, 708) List(0.6402547, 0.66222405, 0.6627116, 0.6643831, 0.6643831, 0.66598743, 0.6690852, 0.6700981, 0.6715667, 0.67226356)